#### Author: Thejasvi Beleyur
#### Last updated: 07-02-2020

This notebook will detail all the steps required to get matching audio snippets for the annotations of bat flights made for 2018-08-17 between 05:00-06:00 hours. 

This notebook is basically a copy of the one used to get annotation audio for 2018-08-17 3-4am. 

### Steps carried out before hand:
1. Generating the video sync for the video file *OrlovaChukaDome_02_20180817_05.00.00-06.00.00...* with frame-wise light intensities and time stamps

2. Video annotations of the horseshoebats flying done by Neetash MR and Aditya Kanjoor. 


In [5]:
import matplotlib.pyplot as plt
import pandas as pd 
from tqdm import tqdm

package_folder = 'C:\\Users\\tbeleyur\\Documents\\match_audio_to_video\\bin\\'
import os
import sys 
sys.path.append(package_folder) # include the modules in the outer folder in the search path
from process_video_annotations import video_sync_over_annotation_block



In [6]:
# loading the annotations
annotations = pd.read_csv('annotations/corrected_HBC_video_annotations_Aditya/2018-08-17_5-6am_Aditya.csv')

In [7]:
annotations.head()

video_path           annotation_id  \
0  OrlovaChukaDome_02_20180817_05.00.00-06.00.00[...  Aditya_2018-08-17_56_1   
1  OrlovaChukaDome_02_20180817_05.00.00-06.00.00[...  Aditya_2018-08-17_56_2   
2  OrlovaChukaDome_02_20180817_05.00.00-06.00.00[...  Aditya_2018-08-17_56_3   
3  OrlovaChukaDome_02_20180817_05.00.00-06.00.00[...  Aditya_2018-08-17_56_4   
4  OrlovaChukaDome_02_20180817_05.00.00-06.00.00[...  Aditya_2018-08-17_56_5   

   Sampling minute  timestamp from camera      start_timestamp  \
0                0                      2  2018-08-17 05:00:06   
1                0                      2  2018-08-17 05:00:08   
2                0                      2  2018-08-17 05:00:15   
3                0                      2  2018-08-17 05:00:20   
4                0                      2  2018-08-17 05:00:31   

   start_framenumber        end_timestamp  end_framenumber  \
0                 11  2018-08-17 05:00:07                8   
1                  4  2018-08-17 05:00:15                1   
2                 22  2018-08-17 05:00:18               17   
3                 10  2018-08-17 05:00:22               21   
4                  8  2018-08-17 05:00:31               20   

   no. of flying bats bat behaviour  strength (1 - strong, 0-weak)  \
0                   1           NaN                              1   
1                   1           NaN                              1   
2                   1           NaN                              1   
3                   1           NaN                              1   
4                   1           NaN                              1   

  weak in (Behaviour Be, Number Bn)                      Comments  \
0                               NaN                           NaN   
1                               NaN                           NaN   
2                               NaN  One bat was inside the roost   
3                               NaN                           NaN   
4                               NaN                           NaN   

   Details on the comment annotator  
0                     NaN    Aditya  
1                     NaN    Aditya  
2                     NaN    Aditya  
3                     NaN    Aditya  
4                     NaN    Aditya

In [10]:
annots_w_bats = annotations[annotations['no. of flying bats']>0].reset_index(drop=True)

In [12]:
annotations.shape

(207, 15)

In [11]:
annots_w_bats.shape

(207, 15)

In [13]:
annots_w_bats.head()

video_path           annotation_id  \
0  OrlovaChukaDome_02_20180817_05.00.00-06.00.00[...  Aditya_2018-08-17_56_1   
1  OrlovaChukaDome_02_20180817_05.00.00-06.00.00[...  Aditya_2018-08-17_56_2   
2  OrlovaChukaDome_02_20180817_05.00.00-06.00.00[...  Aditya_2018-08-17_56_3   
3  OrlovaChukaDome_02_20180817_05.00.00-06.00.00[...  Aditya_2018-08-17_56_4   
4  OrlovaChukaDome_02_20180817_05.00.00-06.00.00[...  Aditya_2018-08-17_56_5   

   Sampling minute  timestamp from camera      start_timestamp  \
0                0                      2  2018-08-17 05:00:06   
1                0                      2  2018-08-17 05:00:08   
2                0                      2  2018-08-17 05:00:15   
3                0                      2  2018-08-17 05:00:20   
4                0                      2  2018-08-17 05:00:31   

   start_framenumber        end_timestamp  end_framenumber  \
0                 11  2018-08-17 05:00:07                8   
1                  4  2018-08-17 05:00:15                1   
2                 22  2018-08-17 05:00:18               17   
3                 10  2018-08-17 05:00:22               21   
4                  8  2018-08-17 05:00:31               20   

   no. of flying bats bat behaviour  strength (1 - strong, 0-weak)  \
0                   1           NaN                              1   
1                   1           NaN                              1   
2                   1           NaN                              1   
3                   1           NaN                              1   
4                   1           NaN                              1   

  weak in (Behaviour Be, Number Bn)                      Comments  \
0                               NaN                           NaN   
1                               NaN                           NaN   
2                               NaN  One bat was inside the roost   
3                               NaN                           NaN   
4                               NaN                           NaN   

   Details on the comment annotator  
0                     NaN    Aditya  
1                     NaN    Aditya  
2                     NaN    Aditya  
3                     NaN    Aditya  
4                     NaN    Aditya

### Carrying out the common-fps conversion:


In [8]:
# load the video sync file with corrected timestamps
video_sync_file = 'videosync_OrlovaChukaDome_01_20180817_05.00.00-06.00.00[R][@2606][0].avi_[corrected_timestamps]_[signal_checked].csv'
path_to_videosync = os.path.join('raw_sync',
                                 video_sync_file)
video_sync = pd.read_csv(path_to_videosync)

In [14]:
kwargs = {'timestamp_pattern': '%Y-%m-%d %H:%M:%S'}
kwargs['min_fps']= 21 # Hz
kwargs['min_durn'] = 60.0 # seconds 
kwargs['common_fps'] = 25 # Hz
kwargs['output_folder'] = './common_fps/Aditya_annotations/2018-08-16/'

unprocessed_annotations = []

for i, each_annotation in tqdm(annots_w_bats.iterrows()):
    try:
        success = video_sync_over_annotation_block(each_annotation,video_sync, 
                                                     **kwargs)
    except :
        unprocessed_annotations.append(i)
        print('Unable to process annotation: %s'%annots_w_bats['annotation_id'][i])


0it [00:00, ?it/s]C:\Users\tbeleyur\AppData\Local\Continuum\anaconda2\envs\horseshoebat\lib\site-packages\scipy\signal\signaltools.py:2223: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  Y[sl] = X[sl]
C:\Users\tbeleyur\AppData\Local\Continuum\anaconda2\envs\horseshoebat\lib\site-packages\scipy\signal\signaltools.py:2225: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  Y[sl] = X[sl]
C:\Users\tbeleyur\AppData\Local\Continuum\anaconda2\envs\horseshoebat\lib\site-packages\scipy\signal\signaltools.py:2233: FutureWarning: Using a non-tuple sequenc

Saved annotation :Aditya_2018-08-17_56_1


1it [00:05,  5.44s/it]

Saved annotation :Aditya_2018-08-17_56_2


2it [00:11,  5.51s/it]

...

205it [17:00,  4.58s/it]

Unable to process annotation: Aditya_2018-08-17_56_206


206it [17:05,  4.81s/it]

Saved annotation :Aditya_2018-08-17_56_207


207it [17:11,  4.98s/it]


### Matching Audio from the common_fps files

In [15]:
### Finding the matching audio snippet !! 
import glob 
import soundfile as sf
from audio_for_videoannotation import match_video_sync_to_audio, search_for_best_fit

#all_commonfps = glob.glob('common_fps_video_sync*') # get all the relevant common_fps_sync files
all_commonfps = glob.glob('common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56*')
audio_folder = 'C://Users//tbeleyur//Documents//horseshoe_bat//2018-08-16//non_spikey//' # the current folder

# the output folders
audiosync_folder = './sync_audio/'
audioannotation_folder = './annotation_audio/'
fs = 250000 # change according to the recording sampling rate in Hz!! 


In [16]:
all_ccs = []
files_to_run = sorted(all_commonfps)

def generate_matching_audio(each_commonfps, audio_folder, 
                           **kwargs):
    '''
    '''
    print(each_commonfps)
    try:
        video_sync = pd.read_csv(each_commonfps)
        best_audio, syncblock_audio, crosscoef = match_video_sync_to_audio(video_sync, audio_folder, 
                                                                           **kwargs)
        all_ccs.append(crosscoef)
        fname  = os.path.split(each_commonfps)[-1]
        annotation_id = '-'.join(os.path.split(fname)[-1].split('common_fps_video_sync')[-1:])[:-4]

        audiosync_folder = kwargs.get('audiosync_folder', 'sync_audio')
        audioannotation_folder = kwargs.get('audioannotation_folder', 'annotation_audio')

    
        audio_file_base_name = annotation_id+'.WAV'
        sf.write(audiosync_folder+'matching_sync_'+audio_file_base_name, syncblock_audio,fs)
        sf.write(audioannotation_folder+'matching_annotaudio_'+audio_file_base_name, best_audio,fs)
        return(True)
    except:
        print('Could not save ', each_commonfps)
        return(False)



In [17]:
all_commonfps

['common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56_1.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56_10.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56_100.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56_101.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56_102.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56_105.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56_106.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56_107.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56_108.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-17_56_109.csv',
 'common_fps\\Aditya_an

In [18]:
audio_folder

'C://Users//tbeleyur//Documents//horseshoe_bat//2018-08-16//non_spikey//'

In [20]:
for each in all_commonfps:
    generate_matching_audio(each, audio_folder, audio_sync_spikey=False, file_subset=('non_spikey_T0000675',
                                                                                      'non_spikey_T0000744'),
                            audio_fileformat='*.WAV',
                          audiosync_folder='sync_audio/Aditya_annotations/',
                           audioannotation_folder='annotation_audio/Aditya_annotations/')


common_fps\Aditya_annotations\2018-08-16\common_fps_video_syncAditya_2018-08-17_56_1.csv
('video_fps obtained is :', 25)
Did not find user-provided sample rate - getting it from first file that matches format!
('sampling rate is : ', 250000)
.....finding best audio segment.....
('max mins for upsampled video', -0.9239309207368741, 1.0)


  0%|                                                                                                                                                        | 0/69 [00:00<?, ?it/s]

('max mins', -0.9143659941673855, 1.0)


C:\Users\tbeleyur\AppData\Local\Continuum\anaconda2\envs\horseshoebat\lib\site-packages\scipy\signal\signaltools.py:491: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  return x[reverse].conj()
  1%|██                                                                                                                                              | 1/69 [00:09<11:17,  9.96s/it]

('max mins', -0.8905970857626782, 1.0)


...

('max mins', -1.0, 0.9420030211032742)


 99%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉  | 68/69 [08:32<00:07,  7.53s/it]

('max mins', -0.9950948650024375, 1.0)


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 69/69 [08:40<00:00,  7.52s/it]


('Best file pairs are: ', 'non_spikey_T0000708.WAV*non_spikey_T0000709.WAV')
Start and end indices around peak:                  start index: 2450193		          end index: 17700193                  total samples:30015488
('AV Sync was above threshold: ', 0.8767621842563336)
